In [58]:
import requests as rq
from bs4 import BeautifulSoup as bs
import time
import pandas as pd
from tqdm import tqdm
import numpy as np
from fake_useragent import UserAgent


URL = 'https://journal.tinkoff.ru/flows/business-all'
HEADERS = {'user-agent': 'Mozilla/5.0 (Windows NT 10.0; Win64; x64)'
                         ' AppleWebKit/537.36 (KHTML, like Gecko)'
                         ' Chrome/100.0.4896.88 Safari/537.36'}

HOST = 'https://journal.tinkoff.ru/'
FILE = '../tinkoffjournal.csv'






In [60]:
def get_html(url: str) -> rq.models.Response:
    return rq.get(url, headers={'User-Agent': UserAgent().chrome}, timeout=15)

In [62]:
responce = get_html('https://journal.tinkoff.ru/flows/invest/posts/')
type(responce)

requests.models.Response

In [19]:
get_flows_args = {'flow_inner_args': {'name': 'div', 'attrs': {'class': 'inner--K9Svv'}},
                  'flow_topic_args': {'name':'a', 'attrs': {'class': 'item--ALUvj'}},
                  'flow_title_args': {'name': 'h4','attrs': {'class': 'heading--lf0qy'}}
                  }

def get_flows(html: bytes, args: dict) -> pd.DataFrame:
    '''
        Парсинг страницы с потоками https://journal.tinkoff.ru/flows/
        Собирает: названия потоков, топики потоков, ссылки на страницы топиков
    '''
    soup = bs(html,'html.parser')
    print((args['flow_inner_args']))
    items = soup.find_all(**(args['flow_inner_args']))[:2]
    print(f'Всего flows: {len(items)}')
    flow_dict = {'flow_title': [], 'start_topic': [], 'flow_link': []}
    for item in tqdm(items):

        flow_items = item.find_all(**(args['flow_topic_args']))[:2]
        
        for flow_item in flow_items:
            flow_dict['start_topic'].append(flow_item.text)
            flow_link = f"https://journal.tinkoff.ru{flow_item.get('href')}"
            if get_html(f'{flow_link}posts/').status_code == 200:
                flow_dict['flow_link'].append(f'{flow_link}posts/')
            else:
                flow_dict['flow_link'].append(flow_link)
            #flow_dict['flow_link'].append(f"https://journal.tinkoff.ru{flow_item.get('href')}")

        flow_dict['flow_title'] += [item.find(**(args['flow_title_args'])).text] * len(flow_items)
    return pd.DataFrame(flow_dict)


        
flows_page_link = "https://journal.tinkoff.ru/flows/"

html = get_html(flows_page_link).content

#не везде нужно добавлять posts !!!!
flow_df = get_flows(html, get_flows_args)
flow_df['flow_link'].values

{'name': 'div', 'attrs': {'class': 'inner--K9Svv'}}
Всего flows: 2


100%|██████████| 2/2 [00:03<00:00,  1.80s/it]


array(['https://journal.tinkoff.ru/flows/invest/posts/',
       'https://journal.tinkoff.ru/flows/invest-ideas/',
       'https://journal.tinkoff.ru/flows/travel/posts/',
       'https://journal.tinkoff.ru/flows/world-travel/'], dtype=object)

In [55]:
flow_df

flow_title          start_topic  \
0   Инвестиции           Инвестиции   
1   Инвестиции           Инвестидеи   
2  Путешествия          Путешествия   
3  Путешествия  Путешествия по миру   

                                        flow_link  
0  https://journal.tinkoff.ru/flows/invest/posts/  
1  https://journal.tinkoff.ru/flows/invest-ideas/  
2  https://journal.tinkoff.ru/flows/travel/posts/  
3  https://journal.tinkoff.ru/flows/world-travel/

In [20]:
get_flow_news_args = {'article_card_args': {'name': 'div', 'attrs': {'class': 'item--LA1zO'}},
                      'article_link_args': {'name': 'a', 'attrs': {'class': 'link--aKZVS'}},
                      'article_author_args': {'name': 'div', 'attrs': {'class': 'name--ur745'}},
                      'article_date_args': {'name': 'time', 'attrs': {'class':'date--ZZJXU'}},
                      'article_views_args': {'name': 'span', 'attrs': {'class': 'counter--sXVCe'}},
                      'article_title_args': {'name': 'h3', 'attrs': {'class': 'title--Oe3sZ'}},
                      'article_likes_args': {'name': 'span', 'attrs': {'class': 'counter--fwxAj'}},
                      'article_comments_count_args': {'name': 'span', 'attrs': {'class': 'content--WdSlu'}},
                      'article_saves_count_args': {'name': 'button', 'attrs': {'class': 'favorites--y85P0'}},
                      'topic_args': {'name': 'h1', 'attrs': {'class': 'heading--lf0qy'}}
                      }

def get_flow_news(html: bytes, args: dict, links_visited: set) -> pd.DataFrame:
  '''
    Парсинг страницы потока
  '''
  soup = bs(html,'html.parser')
  items = soup.find_all(**(args['article_card_args']))[:3]
  news_dict = {'author': [], 'date': [], 'views': [],
                  'topic': [], 'title': [], 'link': [],
                'likes':[], 'comments_count':[], 'saves_count': []}
    
  print(f'Новостей на странице: {len(items)}')
  bad_items = []
  skipped_news_count = 0
  for item in tqdm(items):
    
    try:
      article_link = 'https://journal.tinkoff.ru' + item.find(**(args['article_link_args'])).get('href')
      if article_link not in links_visited:
        links_visited.add(article_link)
        news_dict['author'].append(item.find(**(args['article_author_args'])).text)
        news_dict['date'].append(item.find(**(args['article_date_args'])).get('datetime'))
        news_dict['views'].append(item.find(**(args['article_views_args'])).text)
        news_dict['title'].append(item.find(**(args['article_title_args'])).text)
        news_dict['link'].append(article_link)
        news_dict['likes'].append(item.find(**(args['article_likes_args'])).text)
        news_dict['comments_count'].append(item.find(**(args['article_comments_count_args'])).text)
        news_dict['saves_count'].append(item.find(**(args['article_saves_count_args'])).text)
      else:
        skipped_news_count += 1
        continue

    except Exception:
        skipped_news_count += 1
        bad_items.append(item)
        continue
  news_dict['topic'] = [soup.find(**(args['topic_args'])).text] * (len(items) - skipped_news_count)
  return pd.DataFrame(news_dict), bad_items

page_link = 'https://journal.tinkoff.ru/flows/invest/posts/page/1'

#html = get_html(page_link)
#df, bad_items = get_flow_news(html, get_flow_news_args)
#df.head()

In [40]:
def parse_flow(flow_link: str, args, links_visited: set):
    flow_df = pd.DataFrame({'author': [], 'date': [], 'views': [],
                            'topic': [], 'title': [], 'link': [],
                            'likes':[], 'comments_count':[], 'saves_count': [], 'flow_page_link': [], 'flow_link': []})
    for page in tqdm(range(1, 2)):
        print('Парсинг страничек')
        time.sleep(3)
        try:
            page_link = f'{flow_link}page/{page}'
            html = get_html(page_link).content
            flow_page_df, bad_items = get_flow_news(html, args, links_visited)
            flow_page_df['flow_page_link'] = [page_link]*flow_page_df.shape[0]
            flow_page_df['flow_link'] = [flow_link]*flow_page_df.shape[0]
            flow_df = pd.concat([flow_df, flow_page_df], ignore_index=True)
            
        except Exception:
            continue

    return flow_df

def pase_flows(flows_links: np.ndarray, args):
    '''
        Парсинг страниц потоков по их ссылкам
    '''
    flows_df = pd.DataFrame({'author': [], 'date': [], 'views': [],
                            'topic': [], 'title': [], 'link': [],
                            'likes':[], 'comments_count':[], 'saves_count': [], 'flow_page_link': [], 'flow_link': []})
    links_visited = set()
    for flow_link in tqdm(flows_links):
        print(len(links_visited))
        print('парсинг потока')
        try:   

            flow_df = parse_flow(flow_link, args, links_visited)
            flows_df = pd.concat([flows_df, flow_df], ignore_index=True)
            
        except Exception:
            continue
    return flows_df

#flow_df = parse_flow()
    

In [41]:
d = pase_flows(flow_df['flow_link'].values, get_flow_news_args)

  0%|          | 0/4 [00:00<?, ?it/s]

0
парсинг потока


Парсинг страничек
Новостей на странице: 3



 25%|██▌       | 1/4 [00:03<00:10,  3.38s/it]

3
парсинг потока


...

Парсинг страничек
Новостей на странице: 3



 75%|███████▌  | 3/4 [00:11<00:03,  3.73s/it]

8
парсинг потока


Парсинг страничек
Новостей на странице: 3



100%|██████████| 4/4 [00:15<00:00,  3.90s/it]


In [42]:
d

author        date views                topic  \
0         Юлия Федорович   2024-03-07    1K           Инвестиции   
1     Алексей Климовский   2024-03-07    8K           Инвестиции   
2     Алексей Климовский   2024-03-05   70K           Инвестиции   
3   Альберт Хабибрахимов   2024-02-05   11K           Инвестидеи   
4          Алсу Закирова   2023-11-28   11K           Инвестидеи   
5            Виктор Джин   2022-11-28    2K           Инвестидеи   
6                  Ольга   2024-03-07    4K          Путешествия   
7      Сергей Червоненко   2024-03-07   925          Путешествия   
8       Татьяна Давыдова   2024-03-07   853  Путешествия по миру   
9         Олеся Кравцова   2024-03-07   153  Путешествия по миру   
10      Ольга Чемоданова   2024-03-05   18K  Путешествия по миру   

                                                title  \
0   Как я инвестирую через краудлендинговые площад...   
1   Как я вложил более 1,2 млн рублей и стабильно ...   
2   Как я положил 800 000 ₽ на вклад под 18,5% год...   
3   «Яндекс» объявил о разделе бизнеса: сумма сдел...   
4   За и против: заменит ли Microsoft российская о...   
5   7 неочевидных валютных пар для торговли на Мос...   
6       Как мы съездили в Тулу из Москвы на один день   
7   Как я бесплатно переночевал в стамбульском She...   
8     Как я посетила музей «Аушвиц-Биркенау» в Польше   
9   Как экономить на авиабилетах с помощью Тинькоф...   
10  Отзывы туристов о Дубае: плохие пляжи, передов...   

                                                 link likes comments_count  \
0   https://journal.tinkoff.ru/a-kak-invest-kraudl...     3              9   
1   https://journal.tinkoff.ru/invested-more-than-...     5             17   
2   https://journal.tinkoff.ru/a-kak-invest-800k-n...    26             79   
3      https://journal.tinkoff.ru/news/yandex-russia/    15             98   
4         https://journal.tinkoff.ru/astra-pros-cons/     9             58   
5      https://journal.tinkoff.ru/short/7-currencies/     6              4   
6   https://journal.tinkoff.ru/v-tulu-iz-moskvy-trip/    10              6   
7   https://journal.tinkoff.ru/besplatno-perenoche...     4              4   
8               https://journal.tinkoff.ru/auschwitz/    30             13   
9     https://journal.tinkoff.ru/spec-tinkoff-travel/     1            ···   
10          https://journal.tinkoff.ru/reviews-dubai/     5             19   

   saves_count                                     flow_page_link  \
0            1  https://journal.tinkoff.ru/flows/invest/posts/...   
1            3  https://journal.tinkoff.ru/flows/invest/posts/...   
2           12  https://journal.tinkoff.ru/flows/invest/posts/...   
3            7  https://journal.tinkoff.ru/flows/invest-ideas/...   
4            8  https://journal.tinkoff.ru/flows/invest-ideas/...   
5            3  https://journal.tinkoff.ru/flows/invest-ideas/...   
6            3  https://journal.tinkoff.ru/flows/travel/posts/...   
7            2  https://journal.tinkoff.ru/flows/travel/posts/...   
8            8  https://journal.tinkoff.ru/flows/world-travel/...   
9            1  https://journal.tinkoff.ru/flows/world-travel/...   
10          11  https://journal.tinkoff.ru/flows/world-travel/...   

                                         flow_link  
0   https://journal.tinkoff.ru/flows/invest/posts/  
1   https://journal.tinkoff.ru/flows/invest/posts/  
2   https://journal.tinkoff.ru/flows/invest/posts/  
3   https://journal.tinkoff.ru/flows/invest-ideas/  
4   https://journal.tinkoff.ru/flows/invest-ideas/  
5   https://journal.tinkoff.ru/flows/invest-ideas/  
6   https://journal.tinkoff.ru/flows/travel/posts/  
7   https://journal.tinkoff.ru/flows/travel/posts/  
8   https://journal.tinkoff.ru/flows/world-travel/  
9   https://journal.tinkoff.ru/flows/world-travel/  
10  https://journal.tinkoff.ru/flows/world-travel/

In [49]:
def get_article_content(link: np.ndarray):
    try:
        html = get_html(link).content
        soup = bs(html,'html.parser')
        article_text = soup.find('div', attrs = {'class':'_articleView_1v9h1_1'}).text
        article_author = soup.find(lambda tag: (tag.name == 'a' or tag.name == 'div')\
                                and tag.get('class') == ['_author_1qoqa_6']).text
        topic_name = soup.find('a', attrs = {'class':'_flow_1xwjy_45'}).text
        return [article_text.replace(article_author, ''), topic_name]
    except:
        return [None, None]

def get_articles_content(article_links: list[str]) -> pd.DataFrame:
    articles_contens = [] 
    for article_link in article_links:
        t = get_article_content(article_link)
        t.append(article_link)
        articles_contens.append(t)
    return pd.DataFrame(articles_contens, columns=['article_text', 'topic_name', 'link'])


In [50]:
articles_content_df = get_articles_content(d['link'].values)
articles_content_df.head()

b'<!DOCTYPE html><html lang="ru" prefix="og: http://ogp.me/ns# article: http://ogp.me/ns/article# fb: http://ogp.me/ns/fb#"><head>  <meta charset="utf-8">  <meta name="viewport" content="width=device-width,initial-scale=1">  <meta name="format-detection" content="telephone=no">  <meta name="referrer" content="no-referrer-when-downgrade">  <link rel="manifest" href="https://static2.tinkoffjournal.ru/manifests/manifest.json">  <link rel="alternate" type="application/rss+xml" href="/feed"><link rel="alternate" type="application/atom+xml" href="/feed/atom/">  <link rel="canonical" href="https://journal.tinkoff.ru/a-kak-invest-kraudlending-bez-defoltov/">  <link rel="dns-prefetch" href="https://static2.tinkoffjournal.ru"><link rel="dns-prefetch" href="https://opis-cdn.tinkoffjournal.ru">  <link rel="dns-prefetch" href="https://img-cdn.tinkoffjournal.ru"><link rel="dns-prefetch" href="https://mc.yandex.ru">  <link rel="preconnect" href="https://static2.tinkoffjournal.ru" crossorigin><link re

article_text              topic_name  \
0  Я коммерческий автор, и в середине 2023 года н...              Инвестиции   
1  📈 Мои актуальные результаты на двух крупнейших...     А как инвестировать   
2  Недавно у меня освободились средства с предыду...              Инвестиции   
3  «Яндекс» объявил о реструктуризации. Нидерланд...  Новости для инвесторов   
4  С 2025 года крупные компании и госорганы должн...             За и против   

                                                link  
0  https://journal.tinkoff.ru/a-kak-invest-kraudl...  
1  https://journal.tinkoff.ru/invested-more-than-...  
2  https://journal.tinkoff.ru/a-kak-invest-800k-n...  
3     https://journal.tinkoff.ru/news/yandex-russia/  
4        https://journal.tinkoff.ru/astra-pros-cons/

In [51]:
articles_content_df

article_text              topic_name  \
0   Я коммерческий автор, и в середине 2023 года н...              Инвестиции   
1   📈 Мои актуальные результаты на двух крупнейших...     А как инвестировать   
2   Недавно у меня освободились средства с предыду...              Инвестиции   
3   «Яндекс» объявил о реструктуризации. Нидерланд...  Новости для инвесторов   
4   С 2025 года крупные компании и госорганы должн...             За и против   
5                                                None                    None   
6   Всем привет, хочу рассказать, чем можно себя з...   Читатели путешествуют   
7   Возникла у меня необходимость отправиться в ст...   Читатели путешествуют   
8   В августе 2022 года я побывала в одном из самы...   Читатели путешествуют   
9   Я летаю четыре — шесть раз в месяц.Раньше я по...             Путешествия   
10  Лучшим временем для отдыха в Дубае считают окт...   Читатели путешествуют   

                                                 link  
0   https://journal.tinkoff.ru/a-kak-invest-kraudl...  
1   https://journal.tinkoff.ru/invested-more-than-...  
2   https://journal.tinkoff.ru/a-kak-invest-800k-n...  
3      https://journal.tinkoff.ru/news/yandex-russia/  
4         https://journal.tinkoff.ru/astra-pros-cons/  
5      https://journal.tinkoff.ru/short/7-currencies/  
6   https://journal.tinkoff.ru/v-tulu-iz-moskvy-trip/  
7   https://journal.tinkoff.ru/besplatno-perenoche...  
8               https://journal.tinkoff.ru/auschwitz/  
9     https://journal.tinkoff.ru/spec-tinkoff-travel/  
10          https://journal.tinkoff.ru/reviews-dubai/

In [52]:
merged_df = d.merge(articles_content_df, on='link', how='left')
merged_df


author        date views                topic  \
0         Юлия Федорович   2024-03-07    1K           Инвестиции   
1     Алексей Климовский   2024-03-07    8K           Инвестиции   
2     Алексей Климовский   2024-03-05   70K           Инвестиции   
3   Альберт Хабибрахимов   2024-02-05   11K           Инвестидеи   
4          Алсу Закирова   2023-11-28   11K           Инвестидеи   
5            Виктор Джин   2022-11-28    2K           Инвестидеи   
6                  Ольга   2024-03-07    4K          Путешествия   
7      Сергей Червоненко   2024-03-07   925          Путешествия   
8       Татьяна Давыдова   2024-03-07   853  Путешествия по миру   
9         Олеся Кравцова   2024-03-07   153  Путешествия по миру   
10      Ольга Чемоданова   2024-03-05   18K  Путешествия по миру   

                                                title  \
0   Как я инвестирую через краудлендинговые площад...   
1   Как я вложил более 1,2 млн рублей и стабильно ...   
2   Как я положил 800 000 ₽ на вклад под 18,5% год...   
3   «Яндекс» объявил о разделе бизнеса: сумма сдел...   
4   За и против: заменит ли Microsoft российская о...   
5   7 неочевидных валютных пар для торговли на Мос...   
6       Как мы съездили в Тулу из Москвы на один день   
7   Как я бесплатно переночевал в стамбульском She...   
8     Как я посетила музей «Аушвиц-Биркенау» в Польше   
9   Как экономить на авиабилетах с помощью Тинькоф...   
10  Отзывы туристов о Дубае: плохие пляжи, передов...   

                                                 link likes comments_count  \
0   https://journal.tinkoff.ru/a-kak-invest-kraudl...     3              9   
1   https://journal.tinkoff.ru/invested-more-than-...     5             17   
2   https://journal.tinkoff.ru/a-kak-invest-800k-n...    26             79   
3      https://journal.tinkoff.ru/news/yandex-russia/    15             98   
4         https://journal.tinkoff.ru/astra-pros-cons/     9             58   
5      https://journal.tinkoff.ru/short/7-currencies/     6              4   
6   https://journal.tinkoff.ru/v-tulu-iz-moskvy-trip/    10              6   
7   https://journal.tinkoff.ru/besplatno-perenoche...     4              4   
8               https://journal.tinkoff.ru/auschwitz/    30             13   
9     https://journal.tinkoff.ru/spec-tinkoff-travel/     1            ···   
10          https://journal.tinkoff.ru/reviews-dubai/     5             19   

   saves_count                                     flow_page_link  \
0            1  https://journal.tinkoff.ru/flows/invest/posts/...   
1            3  https://journal.tinkoff.ru/flows/invest/posts/...   
2           12  https://journal.tinkoff.ru/flows/invest/posts/...   
3            7  https://journal.tinkoff.ru/flows/invest-ideas/...   
4            8  https://journal.tinkoff.ru/flows/invest-ideas/...   
5            3  https://journal.tinkoff.ru/flows/invest-ideas/...   
6            3  https://journal.tinkoff.ru/flows/travel/posts/...   
7            2  https://journal.tinkoff.ru/flows/travel/posts/...   
8            8  https://journal.tinkoff.ru/flows/world-travel/...   
9            1  https://journal.tinkoff.ru/flows/world-travel/...   
10          11  https://journal.tinkoff.ru/flows/world-travel/...   

                                         flow_link  \
0   https://journal.tinkoff.ru/flows/invest/posts/   
1   https://journal.tinkoff.ru/flows/invest/posts/   
2   https://journal.tinkoff.ru/flows/invest/posts/   
3   https://journal.tinkoff.ru/flows/invest-ideas/   
4   https://journal.tinkoff.ru/flows/invest-ideas/   
5   https://journal.tinkoff.ru/flows/invest-ideas/   
6   https://journal.tinkoff.ru/flows/travel/posts/   
7   https://journal.tinkoff.ru/flows/travel/posts/   
8   https://journal.tinkoff.ru/flows/world-travel/   
9   https://journal.tinkoff.ru/flows/world-travel/   
10  https://journal.tinkoff.ru/flows/world-travel/   

                                         article_text              topic_name  
0   Я коммерческий авт

In [59]:
flow_df.merge(merged_df, on='flow_link', how='left').to_csv(FILE)

In [ ]:


# Парсер актуальных новостей
def get_content(html: bytes) -> pd.DataFrame:
    soup = bs(html,'html.parser')
    items = soup.find_all('div', attrs = {'class':'item--b9CGu'})
    news_dict = {'author': [], 'date': [], 'views': [],
                  'topic': [], 'title': [], 'link': [],
                'likes':[], 'comments_count':[], 'saves_amount': []}
    
    print(f'Новостей на странице: {len(items)}')
    bad_items = []

    for item in tqdm(items[:4]):
        time.sleep(3)
        try:
            news_dict['author'].append(item.find('div', attrs = {'class':'name--H8jp2'}).text)
            news_dict['date'].append(item.find('time', attrs = {'class':'date--BiQBs'}).get('datetime'))
            news_dict['views'].append(item.find('div', attrs = {'class':'views--AwSbN'}).text)
            news_dict['topic'].append(item.find('a', attrs = {'class':'flow--Sf0iX'}).text)
            news_dict['title'].append(item.find('h3', attrs = {'class':'title--h5Y_9'}).text)
            news_dict['link'].append(item.find('a', attrs = {'class':'link--hGana'}).get('href'))
            news_dict['likes'].append(item.find('span', attrs = {'class':'counter--JSDtN'}).text)
            news_dict['comments_count'].append(item.find('span', attrs = {'class':'content--corUP'}).text)
            news_dict['saves_amount'].append(item.find('button', attrs = {'class':'favorites--BW3AB'}).text)
        except Exception:
            bad_items.append(item)
            continue
        
    return pd.DataFrame(news_dict), bad_items

page_link = "https://journal.tinkoff.ru/tag/breaking-news/page/1/"

html = get_html(page_link)
df, bad_items = get_content(html)
df.head()